# How to create a project

This tutorial demonstrates how to create a project.

## What is a project?

A project is a speos simulation container that includes parts, material properties, sensor,
sources and simulations.

In this tutorial you will learn how to create a project from scratch or from a pre-defined .speos
file.

In [1]:
import os
from pathlib import Path

from ansys.speos.core import Project, Speos
from ansys.speos.core.sensor import SensorIrradiance
from ansys.speos.core.simulation import SimulationDirect
from ansys.speos.core.source import SourceSurface

# If using docker container
assets_data_path = Path("/app") / "assets"
# If using local server
# assets_data_path = Path().resolve().parent.parent / "tests" / "assets"
# If using a different path
# assets_data_path = Path("path/to/downloaded/example/assets")

## Create connection with speos rpc server

In [2]:
speos = Speos(host="localhost", port=50098)

## New empty project

An empty project can be created by only passing speos rpc server to the Project class.

In [3]:
p = Project(speos=speos)
print(p)

{
    "name": "",
    "description": "",
    "metadata": {},
    "part_guid": "",
    "sources": [],
    "sensors": [],
    "simulations": [],
    "materials": [],
    "scenes": []
}


create feature - e.g. source

In [4]:
source1 = p.create_source(name="Source.1", feature_type=SourceSurface)
source1.commit()

create feature - e.g. sensor

In [5]:
sensor1 = p.create_sensor(name="Sensor.1")
sensor1.commit()

create feature - e.g. optical property

In [6]:
opt_prop1 = p.create_optical_property(name="Material.1")
opt_prop1.commit()

## Read Project

User can read the content of a project via simplily printing the project

In [7]:
print(p)

{
    "sources": [
        {
            "name": "Source.1",
            "metadata": {
                "UniqueId": "8b5c018b-e9a9-43c0-9dc8-e2663a589911"
            },
            "source_guid": "39983094-a94d-4068-8ee7-a18b89a93180",
            "description": "",
            "source": {
                "name": "Source.1",
                "surface": {
                    "luminous_flux": {
                        "luminous_value": 683.0
                    },
                    "intensity_guid": "6026e6b3-97f9-4994-9591-6b4dc453f3b8",
                    "exitance_constant": {
                        "geo_paths": []
                    },
                    "spectrum_guid": "c84277f4-bcc7-4ced-bc0d-f267fc0dfde4",
                    "intensity": {
                        "name": "Source.1.Intensity",
                        "cos": {
                            "N": 1.0,
                            "total_angle": 180.0
                        },
                        "description"

Or, user can use the find_key method to read a specific feature:

In [8]:
for it in p.find_key(key="monochromatic"):
    print(it)

(".sources[.name='Source.1'].source.surface.spectrum.monochromatic", {'wavelength': 555.0})


## Find a feature inside a project

### Use find method with an exact name

If no feature is found, an empty list is returned.

In [9]:
features = p.find(name="UnexistingName")
print(features)

[]


In [10]:
features = p.find(name="Sensor.1")
print(features[0])

{
    "name": "Sensor.1",
    "metadata": {
        "UniqueId": "f7cc5a07-3f79-4a59-9b9e-9f2f16065169"
    },
    "sensor_guid": "22214e2f-2ea6-4c12-bf01-0af6ee6d7d43",
    "description": "",
    "result_file_name": "",
    "sensor": {
        "irradiance_sensor_template": {
            "sensor_type_photometric": {},
            "illuminance_type_planar": {},
            "dimensions": {
                "x_start": -50.0,
                "x_end": 50.0,
                "x_sampling": 100,
                "y_start": -50.0,
                "y_end": 50.0,
                "y_sampling": 100
            },
            "axis_system": [
                0.0,
                0.0,
                0.0,
                1.0,
                0.0,
                0.0,
                0.0,
                1.0,
                0.0,
                0.0,
                0.0,
                1.0
            ],
            "layer_type_none": {},
            "ray_file_type": "RayFileNone",
            "integrati

### Use find method with feature type

Here a wrong type is given: no source is called Sensor.1 in the project

In [11]:
features = p.find(name="Sensor.1", feature_type=SourceSurface)
print(features)

[]


In [12]:
features = p.find(name="Sensor.1", feature_type=SensorIrradiance)
print(features[0])

{
    "name": "Sensor.1",
    "metadata": {
        "UniqueId": "f7cc5a07-3f79-4a59-9b9e-9f2f16065169"
    },
    "sensor_guid": "22214e2f-2ea6-4c12-bf01-0af6ee6d7d43",
    "description": "",
    "result_file_name": "",
    "sensor": {
        "irradiance_sensor_template": {
            "sensor_type_photometric": {},
            "illuminance_type_planar": {},
            "dimensions": {
                "x_start": -50.0,
                "x_end": 50.0,
                "x_sampling": 100,
                "y_start": -50.0,
                "y_end": 50.0,
                "y_sampling": 100
            },
            "axis_system": [
                0.0,
                0.0,
                0.0,
                1.0,
                0.0,
                0.0,
                0.0,
                1.0,
                0.0,
                0.0,
                0.0,
                1.0
            ],
            "layer_type_none": {},
            "ray_file_type": "RayFileNone",
            "integrati

### Use find method with approximation name with regex

find a feature with name starting with Mat

In [13]:
features = p.find(name="Mat.*", name_regex=True)
for feat in features:
    print(str(type(feat)) + " : name=" + feat._name)

<class 'ansys.speos.core.opt_prop.OptProp'> : name=Material.1


find all features without defining any name

In [14]:
features = p.find(name=".*", name_regex=True)
for feat in features:
    print(str(type(feat)) + " : name=" + feat._name)

<class 'ansys.speos.core.source.SourceSurface'> : name=Source.1
<class 'ansys.speos.core.sensor.SensorIrradiance'> : name=Sensor.1
<class 'ansys.speos.core.opt_prop.OptProp'> : name=Material.1


## Delete

This erases the scene content in server database.

This deletes also each feature of the project

In [15]:
p.delete()
print(p)

{
    "name": "",
    "description": "",
    "metadata": {},
    "part_guid": "",
    "sources": [],
    "sensors": [],
    "simulations": [],
    "materials": [],
    "scenes": []
}


As the features were deleted just above -> this returns an empty vector

In [16]:
print(p.find(name="Sensor.1"))

[]


## Create project from pre-defined speos project

Via passing the .speos/.sv5 file path to the Project class.

In [17]:
p2 = Project(
    speos=speos,
    path=str(assets_data_path / "LG_50M_Colorimetric_short.sv5" / "LG_50M_Colorimetric_short.sv5"),
)
print(p2)

{
    "name": "LG_50M_Colorimetric_short",
    "description": "From /app/assets/LG_50M_Colorimetric_short.sv5/LG_50M_Colorimetric_short.sv5",
    "part_guid": "16367cdf-2109-4375-9b9b-23313c68b76c",
    "sources": [
        {
            "name": "Dom Source 2 (0) in SOURCE2",
            "metadata": {
                "UniqueId": "f23ff3b4-81b0-4a47-841f-3ff12fa55819"
            },
            "source_guid": "6e23c0b2-a1f1-44d0-89f5-f17b2ea29521",
            "description": "",
            "source": {
                "name": "Dom Source 2 (0) in SOURCE2",
                "surface": {
                    "radiant_flux": {
                        "radiant_value": 6.590041607465698
                    },
                    "intensity_guid": "e3d073d2-0d0a-4589-8cce-e85d28d4c1cb",
                    "exitance_constant": {
                        "geo_paths": [
                            {
                                "geo_path": "Solid Body in SOURCE2:2920204960/Face in SOURCE2:222",

## Preview the part information

User can check the project part using preview method.

In [18]:
p2.preview()

EmbeddableWidget(value='<iframe srcdoc="<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv=&quot;Content-…

use find_key method to find specific information

In [19]:
for it in p2.find_key(key="surface"):
    print(it)

(".sources[.name='Dom Source 2 (0) in SOURCE2'].source.surface", {'radiant_flux': {'radiant_value': 6.590041607465698}, 'intensity_guid': 'e3d073d2-0d0a-4589-8cce-e85d28d4c1cb', 'exitance_constant': {'geo_paths': [{'geo_path': 'Solid Body in SOURCE2:2920204960/Face in SOURCE2:222', 'reverse_normal': False}]}, 'spectrum_guid': 'f51a5a98-0844-4c9c-852c-714e2e782c9a', 'intensity': {'cos': {'N': 1.0, 'total_angle': 180.0}, 'name': '', 'description': '', 'metadata': {}}, 'spectrum': {'library': {'file_uri': '/app/assets/LG_50M_Colorimetric_short.sv5/Red Spectrum.spectrum'}, 'name': '', 'description': '', 'metadata': {}}})
(".sources[.name='Surface Source (0) in SOURCE1'].source.surface", {'radiant_flux': {'radiant_value': 9.290411220389682}, 'intensity_guid': 'fa1a4e3b-f19a-41d1-83e6-cdec76e76818', 'exitance_constant': {'geo_paths': [{'geo_path': 'Solid Body in SOURCE1:2494956811/Face in SOURCE1:187', 'reverse_normal': False}]}, 'spectrum_guid': '234daa4b-fd1c-468d-b6b4-41b225b1ea6b', 'inte

Use find method to retrieve feature:

e.g. surface source

In [20]:
features = p2.find(name=".*", name_regex=True, feature_type=SourceSurface)
for feat in features:
    print(str(type(feat)) + " : name=" + feat._name)
src = features[1]

<class 'ansys.speos.core.source.SourceSurface'> : name=Dom Source 2 (0) in SOURCE2
<class 'ansys.speos.core.source.SourceSurface'> : name=Surface Source (0) in SOURCE1


modify the surface source, e.g. surface source wavelength:

In [21]:
src.set_spectrum().set_monochromatic(wavelength=550)
src.commit()

Retrieve a simulation feature:

In [22]:
features = p2.find(name=".*", name_regex=True, feature_type=SimulationDirect)
sim_feat = features[0]
print(sim_feat)

{
    "name": "ASSEMBLY1.DS (0)",
    "metadata": {
        "UniqueId": "aabd4657-c265-471a-a509-d5cd604fe0bf"
    },
    "simulation_guid": "57dfc2a0-22de-4148-8da1-368a5db586a2",
    "sensor_paths": [
        "Dom Irradiance Sensor (0)"
    ],
    "source_paths": [
        "Dom Source 2 (0) in SOURCE2",
        "Surface Source (0) in SOURCE1"
    ],
    "description": "",
    "simulation": {
        "direct_mc_simulation_template": {
            "geom_distance_tolerance": 0.05,
            "max_impact": 100,
            "weight": {
                "minimum_energy_percentage": 0.005
            },
            "dispersion": true,
            "colorimetric_standard": "CIE_1931",
            "fast_transmission_gathering": false,
            "ambient_material_uri": ""
        },
        "name": "ASSEMBLY1.DS (0)",
        "metadata": {},
        "description": "",
        "scene_guid": "16bd51f2-452a-4bdf-9b4c-63073fe33983",
        "simulation_path": "ASSEMBLY1.DS (0)",
        "job_type

In [23]:
sim_feat.compute_CPU()

[upload_response {
  info {
    uri: "33ce4086-f072-4b7b-b37f-611bb6bab92a"
    file_name: "ASSEMBLY1.DS (0).Dom Irradiance Sensor (0).xmp"
    file_size: 1470032
  }
  upload_duration {
    nanos: 2687971
  }
}
, upload_response {
  info {
    uri: "c70de12c-f007-4d3d-affe-6b3f85ad83fb"
    file_name: "ASSEMBLY1.DS (0).html"
    file_size: 496642
  }
  upload_duration {
    nanos: 744443
  }
}
]

Preview simulation result (only windows)

In [24]:
if os.name == "nt":
    from ansys.speos.core.workflow.open_result import open_result_image

    open_result_image(
        simulation_feature=sim_feat,
        result_name="ASSEMBLY1.DS (0).Dom Irradiance Sensor (0).xmp",
    )